In [ ]:
!pip install git+https://github.com/haven-jeon/PyKoSpacing.git

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Cloning https://github.com/haven-jeon/PyKoSpacing.git to /tmp/pip-req-build-2x9c1no_
  Running command git clone -q https://github.com/haven-jeon/PyKoSpacing.git /tmp/pip-req-build-2x9c1no_
     |████████████████████████████████| 511.8 MB 29 kB/s 
  Created wheel for pykospacing: filename=pykospacing-0.5-py3-none-any.whl size=2268637 sha256=221235b3248c0b358cecc7a34c0fb5cb7ebe97fb636c722cd2f0ce864c018007
  Stored in directory: /tmp/pip-ephem-wheel-cache-qinam0ds/wheels/79/a0/33/16f2cd03d21f76a663f5d69a0b96f0351335385349136fbd03
Successfully built pykospacing
  Attempting uninstall: tensorflow
    Found existing installation: tensorflow 2.9.2
    Uninstalling tensorflow-2.9.2:
      Successfully uninstalled tensorflow-2.9.2


In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
import pandas as pd

directory = '/content/drive/MyDrive/text/'
metadata = pd.read_json(directory + 'metadata.json', lines=True)

In [ ]:
[keywords for keywords in metadata['keyword_list'] if '세계여행' in keywords]

# Co-occurence based Keyword Clustering
- 있는 정보만 활용
- 문제
  - 1) 새로운 데이터가 들어왔을 때 LV cluster 결과가 달라질 수 있음
  - 2) 새롭게 학습을 진행해야 함

In [ ]:
from collections import Counter

Counter([keyword for keywords in metadata['keyword_list'] for keyword in keywords]).most_common()

[('여행', 33887),
 ('영화', 27058),
 ('사랑', 25177),
 ('에세이', 17629),
 ('그림일기', 15806),
 ('생각', 14254),
 ('공감에세이', 13109),
 ('일상', 11175),
 ('글쓰기', 10086),
 ('감성에세이', 10021),
 ('인생', 8929),
 ('행복', 8472),
 ('연애', 7819),
 ('소설', 7734),
 ('드로잉', 7721),
 ('독서', 7451),
 ('육아', 7253),
 ('그림', 7041),
 ('마음', 7030),
 ('사진', 6686),
 ('리뷰', 6432),
 ('엄마', 6404),
 ('음악', 6089),
 ('스타트업', 5777),
 ('시', 5701),
 ('유럽여행', 5558),
 ('일러스트', 5327),
 ('이별', 5241),
 ('마케팅', 5145),
 ('고양이', 5064),
 ('디자인', 4731),
 ('영화리뷰', 4687),
 ('웹툰', 4646),
 ('IT', 4447),
 ('직장인', 4397),
 ('감성', 4390),
 ('일기', 4330),
 ('사람', 4300),
 ('결혼', 4000),
 ('친구', 3959),
 ('창업', 3917),
 ('회사', 3873),
 ('취업', 3783),
 ('교육', 3719),
 ('감성사진', 3676),
 ('퇴사', 3628),
 ('일본', 3627),
 ('건강', 3500),
 ('세계여행', 3444),
 ('해외여행', 3371),
 ('가족', 3361),
 ('커피', 3355),
 ('다이어트', 3322),
 ('성공', 3280),
 ('시간', 3158),
 ('직장', 3116),
 ('음식', 3081),
 ('운동', 2943),
 ('카페', 2812),
 ('책', 2812),
 ('맛집', 2787),
 ('문학', 2784),
 ('관계', 2773),
 ('가을', 2766),
 

In [ ]:
from itertools import combinations

counted = Counter([tuple(sorted(k)) for pair in metadata['keyword_list'].apply(lambda x: list(combinations(x, 2))) for k in pair])

In [ ]:
import pandas as pd

counted = pd.DataFrame.from_dict(counted.items())
counted[['n1', 'n2']] = pd.DataFrame(counted.iloc[:,0].tolist(), index=counted.index)
counted.rename(columns={1: 'weight'}, inplace=True)

In [ ]:
counted

0  weight    n1    n2
0           (여행, 호주)     390    여행    호주
1         (국립공원, 여행)      36  국립공원    여행
2         (국립공원, 호주)       2  국립공원    호주
3        (목련꽃, 아지랑이)       1   목련꽃  아지랑이
4          (동행, 목련꽃)       1    동행   목련꽃
...              ...     ...   ...   ...
705972     (책임감, 화분)       1   책임감    화분
705973      (3D, UI)       1    3D    UI
705974     (3D, 제스처)       1    3D   제스처
705975  (경험수집, 독서모임)       1  경험수집  독서모임
705976   (경험수집, 글쓰기)       1  경험수집   글쓰기

[705977 rows x 4 columns]

In [ ]:
import networkx as nx

G = nx.from_pandas_edgelist(counted, 'n1', 'n2', 'weight')

In [ ]:
print(nx.info(G))

Graph with 85894 nodes and 705977 edges


In [ ]:
import matplotlib.pyplot as plt
from community import community_louvain

'''
https://dc.uwm.edu/cgi/viewcontent.cgi?article=1130&context=ijger
에 따르면 키워드 네트워크에 대해 LV이 가장 성능이 좋으며 시간 복잡도도 낮은 편
'''

partition = community_louvain.best_partition(G)

In [ ]:
# set(partition.values()) # 599
# Counter(partition.values())

[k for k, v in partition.items() if v == 2]

['베네수엘라',
 '경제',
 '유치권',
 '주거문화',
 '부동산',
 '적자',
 '강제집행',
 '부동산경매',
 '개봉동',
 '경매',
 '플래카드',
 '사드',
 '평화',
 '김제동',
 '헌법',
 '분쟁',
 '노무현',
 '대통령',
 '노무현입니다',
 '박근혜',
 '블랙리스트',
 '유신헌법',
 '정치',
 '광화문',
 '촛불',
 '유가',
 '주식투자',
 '박원순',
 '서울시장',
 '조류충돌',
 '조류충돌예방',
 '제도',
 '사전투표',
 '투표용지',
 '수출',
 '살림살이',
 '경제학',
 '명도',
 '예산',
 '아파트',
 '동소문동',
 '시연',
 '자본주의',
 '세월호',
 '투자',
 '투자원칙',
 '주식',
 '신용카드소득공제',
 '절세',
 '세금',
 '판사',
 '권력관계',
 '권력',
 '강남',
 '원격의료',
 '노래모임',
 '촛불집회',
 '성주촛불',
 '하멜른',
 '피리',
 '부자',
 '재테크',
 '서울시',
 '소비',
 '절약',
 '추모',
 '법관',
 '선거',
 '법원경매',
 '입찰보증금',
 '민주주의',
 '대박',
 '가계부',
 '신용카드',
 '임팩트',
 '출마',
 '패거리문화',
 '통장',
 '총학생회',
 '공청회',
 '대선',
 '공약집',
 '이사',
 '정주영',
 '국회의원',
 '안철수',
 '미분양',
 '재산세',
 '경제불황',
 '김영란',
 '청탁',
 '도널드트럼프',
 '버락오바마',
 '썰전',
 '저축',
 '서울도서관',
 '서울시청',
 '지자체',
 '금리',
 '단기채권',
 '시중은행',
 '북한',
 '박정희',
 '민주공화국',
 '부동산뉴스',
 '무료취업지원',
 '생애설계',
 '사옥',
 '임대수익률',
 '재건축',
 '도시재생프로젝트',
 '도시재생',
 '국회',
 '대출신청',
 '전세자금',
 '김정은',
 '트럼프',
 '정상회담',
 '금융상품',
 '장기금융시장',
 '파

In [ ]:
metadata['keyword_cluster'] = metadata['keyword_list'].apply(lambda x: set([partition[keyword] if keyword in partition.keys() else -1 for keyword in x]))

In [ ]:
Counter(metadata['keyword_cluster'].apply(len))

Counter({1: 277163, 2: 236056, 0: 70065, 3: 59759, 4: 61})

# SPARQL ontology
- 외부 정보 활용
- 문제
  - 동음이의어 문제

In [ ]:
!pip install sparqlwrapper

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 500 kB 65.4 MB/s 
     |████████████████████████████████| 41 kB 643 kB/s 


In [ ]:
def sparql_query(query_search):

    # query = """
    #     PREFIX dbo:  <http://dbpedia.org/ontology/>
    #     PREFIX dbpedia: <http://ko.dbpedia.org/resource/>
    #     PREFIX dbp: <http://ko.dbpedia.org/property/>
    #     PREFIX dcterms: <http://purl.org/dc/terms/>
    #     PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>

    #     SELECT distinct (?subject||?redirects) ?comment ?category
    #       WHERE {
    #           ?subject rdfs:comment ?comment.
    #           ?subject dcterms:subject ?category.
    #           ?redirects dbo:wikiPageRedirects* ?subject.
    #           FILTER (?subject = dbpedia:%s || ?redirects = dbpedia:%s)
    #     }
    #     """ % (query_search, query_search)

    query = """
        PREFIX dbo:  <http://dbpedia.org/ontology/>
        PREFIX dbpedia: <http://ko.dbpedia.org/resource/>
        PREFIX dbp: <http://ko.dbpedia.org/property/>
        PREFIX dcterms: <http://purl.org/dc/terms/>
        PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>

        SELECT * WHERE
        {
          {
            SELECT distinct ?subject ?comment ?category WHERE {
              ?subject rdfs:comment ?comment.
              ?subject dcterms:subject ?category.
              FILTER (?subject = dbpedia:%s)
            }
          }
          UNION
          {
            SELECT distinct ?redirects ?comment ?category WHERE {
              ?subject rdfs:comment ?comment.
              ?subject dcterms:subject ?category.
              ?redirects dbo:wikiPageRedirects* ?subject.
              FILTER (?redirects = dbpedia:%s)
              }
            }
        }
        """ % (query_search, query_search)

    sparql = SPARQLWrapper("http://ko.dbpedia.org/sparql")
    sparql.setQuery(query)

    sparql.setReturnFormat(JSON)
    results = sparql.query().convert()

    return results


In [ ]:
from SPARQLWrapper import SPARQLWrapper, JSON
import pandas as pd
from collections import Counter
from tqdm import tqdm
import pickle

# queries_tosearch = [item[0] for item in Counter([keyword for keywords in metadata['keyword_list'] for keyword in keywords]).most_common(50)]
queries_tosearch = set([keyword for keywords in metadata['keyword_list'] for keyword in keywords])
print('Search for...', queries_tosearch)

searched_results = pd.DataFrame()
searched_dict = {}
error_list = {'no_results': [], 'error': []}

for i, query_search in tqdm(enumerate(queries_tosearch)):
    try:
        if query_search not in (set(error_list['no_results']) | set(error_list['error'])):
            results = sparql_query(query_search)
            results_df = pd.json_normalize(results['results']['bindings'])
            # if any(results_df.columns.str.contains('subject.value')):
            #     print(str(i)+'.',query_search, '---->', results_df.shape[0], '건 (Subject)')
            # elif any(results_df.columns.str.contains('redirects.value')):
            #     print(str(i)+'.',query_search, '---->', results_df.shape[0], '건 (Redirects)')
            searched_results = searched_results.append(results_df.loc[:, results_df.columns.str.contains("value")])
            if results_df.shape[0]>0:
                searched_dict[query_search] = set(results_df['category.value'].apply(lambda x: x.replace('http://ko.dbpedia.org/resource/분류:', '')))
            else:
                # new_query_search = spacing(query_search).replace(' ', '_')  
                new_query_search = query_search
                if new_query_search == query_search:
                    # print('-----------------> No results for:', query_search)
                    error_list['no_results'].append(query_search)
                else:
                    # print('-----------------> No results for:', query_search, "=>", new_query_search)
                    error_list['no_results'].append(query_search)
        if i%100 == 0:
            with open(directory + 'error_list.pickle', 'wb') as handle:
                pickle.dump(error_list, handle, protocol=pickle.HIGHEST_PROTOCOL)
            with open(directory + 'searched_dict.pickle', 'wb') as handle:
                pickle.dump(searched_dict, handle, protocol=pickle.HIGHEST_PROTOCOL)


    except Exception as ex:
        # new_query_search = spacing(query_search).replace(' ', '_')
        print('-----------------> Error:', query_search)
        error_list['error'].append(query_search)

if any(searched_results.columns.str.contains('redirects.value')):
    searched_results = searched_results.drop_duplicates(['redirects.value', 'category.value']).reset_index(drop=True)
if any(searched_results.columns.str.contains('subject.value')):
    searched_results = searched_results.drop_duplicates(['subject.value', 'category.value']).reset_index(drop=True)

Search for... {'물가수준', '리베이트', '편강', '스토브', '임야구입', '울랄라세션', '예정화', '반성글', '조엘오스틴', '도시경제학', '고객서비스', '입시미술', '장르소설', '경주양동마을', '우다이푸르', '바이오의약품', '챗봇서비스', '토론준비', '윤리에세이', '금융공황', '명랑이발관', '씀바귀꽃', '논리철학', '싱가포르뮤직페스티벌', '집안사정', '아침가리', '공의반란', '기사문', '멜로딕데스메탈', '중이염증상', '문화유산보전', '자아도취', '길가', '민족개벽', '셔터스톡', '복소수', '검색포털', '도날드', '대만쇼핑', '시간차', '인문기행', '모둠활동', '노잼', '초능력', '농촌행복복합마을', '생리통', '한국가구', '일치', '뷰티웹툰', '테니스', '전공교육과정', '도그빌', '경력변화전문가', '수사능력', '나무토막', '파리스토리', '기대감', '내수활성화', '아마존ceo', '로빈슨', '은하공책폭탄', '독일새댁', '로렉스', '화랑도서관', '아트콜라보', '타겟팅', '유통혁명', '갑신정변', '음주운전교통사고', '소방박물관', '예비돌싱녀', '풍선마술사', '체인본사', '교통위반', '셀폰', '청춘여행', '이치우미', '개인연금', '선리기연', '대화주제', '파밍로드', '과일', '윤석민', '야채볶음', '시월노트', '스티브', '스테판커리', '맛집정보', '레몬하트', '토종효모빵', '로미오줄리엣', '육아퇴직', '절', '초혼', '피레네산맥', '지진대비', '카디건', '공항픽업', '경희사이버대학교', '빙빙', '부친', '증후군', '일반화', '웨딩카드', '문화한국', '추적자', '헤이즐넛', '독서자본', '법인회생절차', '평화통일교육', '디모데', '기부금영수증', '편집증', '글제목', '권리해태', '배당금지급채권', '부동산거래위임장', '트랜스지방', '주요업무계획', '어혈',

383it [01:10,  6.03it/s]

-----------------> Error: 주식매각


386it [01:10,  6.04it/s]

-----------------> Error: 아해


...

85796it [5:03:28,  4.64it/s]

-----------------> Error: 크루그먼


85799it [5:03:29,  4.44it/s]

-----------------> Error: 인천여중생


86037it [5:04:28,  4.71it/s]


In [ ]:
with open(directory + 'error_list_final.pickle', 'wb') as handle:
    pickle.dump(error_list, handle, protocol=pickle.HIGHEST_PROTOCOL)
with open(directory + 'searched_dict_final.pickle', 'wb') as handle:
    pickle.dump(searched_dict, handle, protocol=pickle.HIGHEST_PROTOCOL)

In [ ]:
error_list['no_results']

['물가수준',
 '편강',
 '임야구입',
 '반성글',
 '조엘오스틴',
 '도시경제학',
 '고객서비스',
 '입시미술',
 '장르소설',
 '바이오의약품',
 '챗봇서비스',
 '토론준비',
 '윤리에세이',
 '금융공황',
 '명랑이발관',
 '논리철학',
 '싱가포르뮤직페스티벌',
 '집안사정',
 '아침가리',
 '공의반란',
 '기사문',
 '중이염증상',
 '문화유산보전',
 '길가',
 '민족개벽',
 '복소수',
 '검색포털',
 '도날드',
 '대만쇼핑',
 '시간차',
 '인문기행',
 '모둠활동',
 '노잼',
 '농촌행복복합마을',
 '일치',
 '뷰티웹툰',
 '전공교육과정',
 '경력변화전문가',
 '수사능력',
 '나무토막',
 '파리스토리',
 '기대감',
 '내수활성화',
 '아마존ceo',
 '로빈슨',
 '은하공책폭탄',
 '독일새댁',
 '화랑도서관',
 '아트콜라보',
 '타겟팅',
 '유통혁명',
 '음주운전교통사고',
 '소방박물관',
 '예비돌싱녀',
 '풍선마술사',
 '체인본사',
 '청춘여행',
 '이치우미',
 '개인연금',
 '대화주제',
 '파밍로드',
 '윤석민',
 '야채볶음',
 '시월노트',
 '스티브',
 '스테판커리',
 '맛집정보',
 '레몬하트',
 '토종효모빵',
 '로미오줄리엣',
 '육아퇴직',
 '절',
 '피레네산맥',
 '지진대비',
 '공항픽업',
 '빙빙',
 '일반화',
 '웨딩카드',
 '문화한국',
 '독서자본',
 '법인회생절차',
 '평화통일교육',
 '기부금영수증',
 '글제목',
 '권리해태',
 '배당금지급채권',
 '부동산거래위임장',
 '주요업무계획',
 '어혈',
 '크롤러',
 '투자자조합원',
 '듀엣곡',
 '수중사진작가',
 '집세',
 '폰트서체',
 '포토라인',
 '프란체스카',
 '토지계약서',
 '규칙동사',
 '리스회계',
 '가마블럭',
 '내장사',
 '방콕여행코스',
 '유럽여행팁',
 '하늘존재감',
 '아프로',
 '김기창',


In [ ]:
searched_results['subject'] = searched_results[['subject.value', 'redirects.value']].fillna('').sum(axis=1).apply(lambda x: x.replace('http://ko.dbpedia.org/resource/', ''))
searched_results = searched_results[['subject', 'comment.value', 'category.value']].drop_duplicates()
searched_results['category.value'] = searched_results['category.value'].apply(lambda x: x.replace('http://ko.dbpedia.org/resource/분류:', ''))
searched_results = searched_results.groupby(['subject', 'comment.value']).agg({'category.value':lambda x: list(x)}).reset_index()

In [ ]:
import pandas as pd
searched_results.to_csv(directory + 'searched_results_ontoloy.csv', index=False)

In [ ]:
import pandas as pd

searched_results = pd.read_csv(directory + 'searched_results_ontoloy_updated.csv')

In [ ]:
import pickle

with open(directory + 'error_list_final.pickle', 'rb') as handle:
    error_list = pickle.load(handle)
with open(directory + 'searched_dict_final.pickle', 'rb') as handle:
    searched_dict = pickle.load(handle)

In [ ]:
searched_results

subject                                      comment.value  \
0        11번가  11번가(11st)는 2008년 2월 사업을 시작한 대한민국 오픈 마켓으로, 201...   
1         11월  11월은 그레고리력에서 한 해의 열한 번째 달이며, 30일까지 있다. 이 달과 그 ...   
2         12월  12월은 그레고리력에서 한 해의 열두 번째 달이며, 31일까지 있다. 한국, 중국,...   
3      1차세계대전  제1차 세계 대전(第一次世界大戰, World War I, 1914년 7월 28일 ~...   
4        21세기                        21세기는 2001년부터 2100년까지를 말한다.   
...       ...                                                ...   
22577     NaN  오프라 윈프리(Oprah Gail Winfrey, 1954년 1월 29일 ~ )는 ...   
22578     NaN  오프라 윈프리(Oprah Gail Winfrey, 1954년 1월 29일 ~ )는 ...   
22579     NaN  오프라 윈프리(Oprah Gail Winfrey, 1954년 1월 29일 ~ )는 ...   
22580     NaN  오프라 윈프리(Oprah Gail Winfrey, 1954년 1월 29일 ~ )는 ...   
22581     NaN  오프라 윈프리(Oprah Gail Winfrey, 1954년 1월 29일 ~ )는 ...   

                                          category.value  \
0                                     ['SK그룹', '온라인_서점']   
1                                                ['11월']   
2                                                ['12월']   
3      ['뉴질랜드의_전쟁', '미국의_역사_(1865-1918)', '오스트레일리아의_전...   
4                                               ['21세기']   
...                                                  ...   
22577           http://ko.dbpedia.org/resource/분류:시카고_출신   
22578        http://ko.dbpedia.org/resource/분류:아프리카계_미국인   
22579          http://ko.dbpedia.org/resource/분류:여성_억만장자   
22580  http://ko.dbpedia.org/resource/분류:미국의_텔레비전_토크_...   
22581          http://ko.dbpedia.org/resource/분류:오프라_윈프리   

                              redirects.value subject.value  
0                                         NaN           NaN  
1                                         NaN           NaN  
2                                         NaN           NaN  
3                                         NaN           NaN  
4                                         NaN           NaN  
...                                       ...           ...  
22577  http://ko.dbpedia.org/resource/오프라_윈프리           NaN  
22578  http://ko.dbpedia.org/resource/오프라_윈프리           NaN  
22579  http://ko.dbpedia.org/resource/오프라_윈프리           NaN  
22580  http://ko.dbpedia.org/resource/오프라_윈프리           NaN  
22581  http://ko.dbpedia.org/resource/오프라_윈프리           NaN  

[22582 rows x 5 columns]

In [ ]:
from SPARQLWrapper import SPARQLWrapper, JSON
import pandas as pd
from collections import Counter
from tqdm import tqdm
from pykospacing import Spacing
import pickle

spacing = Spacing()

for i, query_search in tqdm(enumerate(error_list['no_results'])):
    try:
        if i > 54297:
            new_query_search = spacing(query_search).replace(' ', '_')
            if new_query_search != query_search:
                results = sparql_query(new_query_search)
                results_df = pd.json_normalize(results['results']['bindings'])
                searched_results = searched_results.append(results_df.loc[:, results_df.columns.str.contains("value")])
                if results_df.shape[0]>0:
                    print(query_search, "=>", new_query_search)
                    searched_dict[query_search] = set(results_df['category.value'].apply(lambda x: x.replace('http://ko.dbpedia.org/resource/분류:', '')))
                    error_list['no_results'].remove(query_search)
                    if query_search in error_list['error']:
                        error_list['error'].remove(query_search)

            if i%30 == 0:
                searched_results.to_csv(directory + 'searched_results_ontoloy_updated.csv', index=False)

    except Exception as ex:
        # new_query_search = spacing(query_search).replace(' ', '_')
        # print(ex)
        print('-----------------> Error:', query_search)

0it [00:00, ?it/s]

1/1 [==============================] - 0s 450ms/step


54299it [00:00, 55855.87it/s]

1/1 [==============================] - 0s 22ms/step
김종욱찾기 => 김종욱_찾기
1/1 [==============================] - 0s 22ms/step
실크스크린 => 실크_스크린
1/1 [==============================] - 0s 19ms/step
앙리마티스 => 앙리_마티스
1/1 [==============================] - 0s 27ms/step


54386it [00:20, 1913.16it/s] 

...

62148it [31:49,  4.50it/s]

1/1 [==============================] - 0s 39ms/step


62149it [31:50,  3.57it/s]

1/1 [==============================] - 0s 44ms/step


62151it [31:50, 32.53it/s]


In [ ]:
import pandas as pd
searched_results.to_csv(directory + 'searched_results_ontoloy_updated.csv', index=False)

## Keyword - Category Matrix
- 키워드의 '분류' 정보를 매트릭스로 나타냄

In [ ]:
searched_dict

{'여행': {'여행'},
 '영화': {'영화'},
 '사랑': {'사랑'},
 '에세이': {'수필'},
 '그림일기': {'2000년_영화',
  '대한민국의_드라마_영화',
  '대한민국의_영화_작품',
  '대한민국의_코미디_영화',
  '한국어_영화_작품'},
 '생각': {'생각'},
 '글쓰기': {'글짓기', '문학', '쓰기'},
 '인생': {'인간의_발달_과정', '인생'},
 '행복': {'행복'},
 '연애': {'로맨스', '사랑'},
 '소설': {'소설'},
 '독서': {'인간_행동', '읽기'},
 '그림': {'회화'},
 '마음': {'마음', '심리학'},
 '사진': {'사진'},
 '엄마': {'가족', '성과_사회', '여성', '여성을_가리키는_용어', '인간의_성'},
 '음악': {'음악'},
 '스타트업': {'기업', '산업'},
 '일러스트': {'삽화', '회화'},
 '이별': {'1973년_영화', '대한민국의_영화_작품', '한국어_영화_작품'},
 '마케팅': {'마케팅', '영어계_외래어'},
 '고양이': {'고양이', '고양이속', '모델_생물'},
 '디자인': {'디자인'},
 '영화리뷰': {'영화_평론'},
 '웹툰': {'만화', '웹툰', '전자_출판'},
 '직장인': {'상태별_사람', '오피스'},
 '감성': {'심리학', '철학'},
 '일기': {'문학', '일기'},
 '사람': {'사람', '유인원'},
 '결혼': {'결혼식', '성과_사회', '인간의_성', '인류의_진화', '혼인'},
 '친구': {'우정', '인간_관계'},
 '창업': {'기업_윤리', '기업인'},
 '회사': {'기업', '법인', '상법'},
 '교육': {'교육', '의무'},
 '일본': {'경제_협력_개발_기구_회원국', '국제_연합_회원국', '유엔_회원국', '일본', '입헌군주국'},
 '건강': {'건강'},
 '해외여행': {'국제_교류', '여행의_형태'},
 '가족'

In [ ]:
import numpy as np

tmp_dict = {}
s = set([val for vals in searched_dict.values() for val in vals])

for k, v in searched_dict.items():
    tmp_dict[k] = [1 if s_ in v else 0 for s_ in s]

In [ ]:
TDM = pd.DataFrame.from_dict(tmp_dict,orient='index')
TDM.columns = s

In [ ]:
TDM

교육  피지의_언어  예술  마케팅  교육심리학  생명  소설  고양이  마음  겨울  ...  철학  유인원  모리셔스의_언어  \
여행     0       0   0    0      0   0   0    0   0   0  ...   0    0         0   
영화     0       0   0    0      0   0   0    0   0   0  ...   0    0         0   
사랑     0       0   0    0      0   0   0    0   0   0  ...   0    0         0   
에세이    0       0   0    0      0   0   0    0   0   0  ...   0    0         0   
그림일기   0       0   0    0      0   0   0    0   0   0  ...   0    0         0   
...   ..     ...  ..  ...    ...  ..  ..  ...  ..  ..  ...  ..  ...       ...   
시작     0       0   0    0      0   0   0    0   0   0  ...   0    0         0   
오늘     0       0   0    0      0   0   0    0   0   0  ...   0    0         0   
삶      0       0   0    0      0   1   0    0   0   0  ...   0    0         0   
브런치    0       0   0    0      0   0   0    0   0   0  ...   0    0         0   
인간     0       0   0    0      0   0   0    0   0   0  ...   0    1         0   

      잠  뉴욕_주의_도시  프랑스  헤비_메탈_음반  뉴질랜드의_언어  커피하우스  법인  
여행    0         0    0         0         0      0   0  
영화    0         0    0         0         0      0   0  
사랑    0         0    0         0         0      0   0  
에세이   0         0    0         0         0      0   0  
그림일기  0         0    0         0         0      0   0  
...  ..       ...  ...       ...       ...    ...  ..  
시작    0         0    0         1         0      0   0  
오늘    0         0    0         0         0      0   0  
삶     0         0    0         0         0      0   0  
브런치   0         0    0         0         0      0   0  
인간    0         0    0         0         0      0   0  

[109 rows x 270 columns]

In [ ]:
from scipy.spatial.distance import cdist

np.where(((1 - cdist(TDM, TDM, metric='cosine')) - np.eye(TDM.shape[0])) == 1)

(array([ 0, 52]), array([52,  0]))

In [ ]:
TDM.index[0], TDM.index[52]

('여행', '배낭여행')

## Comment Semantic Representation

In [ ]:
!pip install sentence_transformers

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 85 kB 3.2 MB/s 
     |████████████████████████████████| 5.5 MB 39.6 MB/s 
     |████████████████████████████████| 1.3 MB 59.1 MB/s 
     |████████████████████████████████| 182 kB 63.4 MB/s 
     |████████████████████████████████| 7.6 MB 40.5 MB/s 
  Created wheel for sentence-transformers: filename=sentence_transformers-2.2.2-py3-none-any.whl size=125938 sha256=c8a9bb32eedf1fdb22f3d86c45fc09200d0455f6be6b9c11a58c337793ba018f
  Stored in directory: /root/.cache/pip/wheels/bf/06/fb/d59c1e5bd1dac7f6cf61ec0036cc3a10ab8fecaa6b2c3d3ee9
Successfully built sentence-transformers


In [ ]:
from sentence_transformers import SentenceTransformer, util

'''
https://github.com/snunlp/KR-SBERT
'''

model = SentenceTransformer('snunlp/KR-SBERT-V40K-klueNLI-augSTS') 

Downloading:   0%|          | 0.00/1.23k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/190 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/4.02k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/707 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/124 [00:00<?, ?B/s]

...

Downloading:   0%|          | 0.00/112 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/967k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/394 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/336k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/229 [00:00<?, ?B/s]

## Document to Embedding vectors
- 자기가 속한 키워드 상위계층의 comment를 encoding해서 그걸 키워드 벡터로 써도 될듯. 만약 여러개라면 aggregate/pooling (max, min, avg)

In [ ]:
searched_results = searched_results[['subject', 'comment.value', 'category.value']].drop_duplicates(['subject']).reset_index(drop=True)

In [ ]:
searched_results['comment.value']

0     여행(旅行, 문화어: 려행)이란 일이나 유람을 목적으로 다른 고장이나 외국에 가는 ...
1     영화(映畵, film)는 순간을 기록한 장면을 연속하여 촬영하여 기록한 동영상을 같...
2     사랑은 좋아하고 아끼는 마음을 말한다. 대표적인 예로 모성애나, 가족, 또는 연인에...
3     수필(隨筆) 또는 에세이(essay)는 생각을 자유롭게 표현한 산문 문학이다. 주제...
4                        《그림일기》는 2000년에 개봉한 대한민국의 영화이다.
5     생각은 결론을 얻으려는 관념의 과정이다. 목표에 이르는 방법을 찾으려고 하는 정신 ...
6     글짓기는 정보 전달을 목적으로 문장을 정리하여 글을 지어나가는 행위를 말한다. 글을...
7     인생(人生, 영어: life)은 사람이 세상에서 사는 것과 살아있는 시간, 경험 등이다.
8     행복(幸福, 영어: hapiness)은 욕구와 욕망이 충족되어 만족하거나 즐거움을 ...
9     연애(戀愛)는 서로를 사랑하는 두 사람(이들을 연인이라 한다) 사이의 친밀한 관계를...
10    소설(小說)은 허구적인 인물과 사건을 순차적인 이야기로 묘사한 산문이다. 서사시에서...
11    읽기는 인쇄된 문자나 글로 쓴 것으로부터 뜻을 얻어내는 인지 과정이다. 그리고 책 ...
12    회화(繪畵)는 켄버스, 종이, 나무, 유리, 비단, 콘크리트 등의 표면에 색을 이용...
13    마음은 사람이 다른 사람이나 사물에 대하여 생각, 인지, 기억, 감정, 의지, 그리...
14    물리학적으로 사진(寫真 또는 光畵, Photography)은 물체에서 반사된 빛과 ...
15    어머니(母, Mother, Mom)또는 어머님, 어미, 엄마, 모친(母親)은 자손을...
16    음악(音樂)은 한자어에서 짐작할 수 있듯이 소리로서 혹은 소리를 들음으로써 사람이 ...
17    스타트업 컴퍼니(영어: startup company) 또는 스타트업(영어: 

In [ ]:
sentences = searched_results['comment.value']
vectors = model.encode(sentences) # encode sentences into vectors

In [ ]:
vectors.shape

(37, 768)

In [ ]:
tmp = dict(zip(searched_results['subject'], vectors))

In [ ]:
doc_emb_dict = {}
for i, keywords in zip(metadata['id'], metadata['keyword_list']):
  doc_emb_dict[i] = sum([tmp[k] for k in keywords if k in tmp.keys()])

In [ ]:
doc_emb_dict

{'@bookdb_782': array([-8.66051853e-01,  3.95523757e-01, -8.76173258e-01, -1.26843601e-01,
        -1.37788713e-01,  5.77976048e-01, -4.95925367e-01, -4.22522992e-01,
        -2.40016595e-01,  3.45324248e-01,  4.78045754e-02, -1.30546737e+00,
         2.34782159e-01,  1.49249077e-01, -7.13518500e-01, -5.78768492e-01,
         2.39754245e-01,  4.54811007e-01, -1.54140308e-01,  9.50988084e-02,
        -3.99935365e-01,  6.07285474e-04, -7.68026114e-01,  2.74620503e-01,
         2.59626489e-02, -6.97862059e-02, -1.83994085e-01,  1.14919519e+00,
        -1.31499752e-01,  3.96462739e-01, -2.35135093e-01, -9.16511297e-01,
         5.60251102e-02,  5.71412802e-01,  1.78536832e-01, -6.46907091e-01,
        -4.71778482e-01,  1.73632845e-01,  9.25283507e-02,  3.28273892e-01,
        -8.25371087e-01, -6.32422626e-01,  2.91401148e-01, -4.55574960e-01,
         1.02595843e-01,  3.26436609e-01,  7.65867293e-01, -6.26566112e-01,
         4.52749342e-01,  1.14323485e+00, -2.66001821e-01,  1.33934057e+0

## Similarities Between Vectors
- 음 근데 comment끼리 유사도를 구하면 pair level인데 이걸 어떻게 활용할 수 있을까? clustering을 해야하나?

In [ ]:
similarities = util.cos_sim(vectors, vectors) # compute similarity between sentence vectors
print(similarities)

tensor([[1.0000, 0.2886, 0.3782,  ..., 0.3104, 0.2982, 0.2281],
        [0.2886, 1.0000, 0.4301,  ..., 0.4589, 0.4122, 0.3020],
        [0.3782, 0.4301, 1.0000,  ..., 0.4575, 0.5233, 0.3233],
        ...,
        [0.3104, 0.4589, 0.4575,  ..., 1.0000, 0.5144, 0.3421],
        [0.2982, 0.4122, 0.5233,  ..., 0.5144, 1.0000, 0.2058],
        [0.2281, 0.3020, 0.3233,  ..., 0.3421, 0.2058, 1.0000]])


In [ ]:
import numpy as np

similarities_ = (similarities.numpy() - np.eye(similarities.shape[0]))
similarities_max = np.argwhere((similarities.numpy() - np.eye(similarities.shape[0])) == similarities_.max(5).item())

In [ ]:
similarities_.max(5)

In [ ]:
similarities_max

array([[45, 65],
       [65, 45]])

In [ ]:
searched_results.subject[similarities_max[1]]

65    겨울
45    가을
Name: subject, dtype: object

In [ ]:
searched_results.subject[2]

'사랑'

In [ ]:
searched_results.subject[5]

'생각'

In [ ]:
searched_results

subject.value  \
0      http://ko.dbpedia.org/resource/여행   
1                                    NaN   
2      http://ko.dbpedia.org/resource/영화   
3                                    NaN   
4      http://ko.dbpedia.org/resource/사랑   
..                                   ...   
114                                  NaN   
115  http://ko.dbpedia.org/resource/해외여행   
116  http://ko.dbpedia.org/resource/해외여행   
117                                  NaN   
118                                  NaN   

                                         comment.value  \
0    여행(旅行, 문화어: 려행)이란 일이나 유람을 목적으로 다른 고장이나 외국에 가는 ...   
1    여행(旅行, 문화어: 려행)이란 일이나 유람을 목적으로 다른 고장이나 외국에 가는 ...   
2    영화(映畵, film)는 순간을 기록한 장면을 연속하여 촬영하여 기록한 동영상을 같...   
3    영화(映畵, film)는 순간을 기록한 장면을 연속하여 촬영하여 기록한 동영상을 같...   
4    사랑은 좋아하고 아끼는 마음을 말한다. 대표적인 예로 모성애나, 가족, 또는 연인에...   
..                                                 ...   
114  건강(健康, 영어: health)이란 완전한 신체적, 정신적, 사회적 안녕의 상태를...   
115  해외여행(海外旅行) 또는 국외여행(國外旅行)은 외국을 목적지로하는 여행을 말한다. ...   
116  해외여행(海外旅行) 또는 국외여행(國外旅行)은 외국을 목적지로하는 여행을 말한다. ...   
117  해외여행(海外旅行) 또는 국외여행(國外旅行)은 외국을 목적지로하는 여행을 말한다. ...   
118  해외여행(海外旅行) 또는 국외여행(國外旅行)은 외국을 목적지로하는 여행을 말한다. ...   

                               category.value  \
0        http://ko.dbpedia.org/resource/분류:여행   
1        http://ko.dbpedia.org/resource/분류:여행   
2        http://ko.dbpedia.org/resource/분류:영화   
3        http://ko.dbpedia.org/resource/분류:영화   
4        http://ko.dbpedia.org/resource/분류:사랑   
..                                        ...   
114      http://ko.dbpedia.org/resource/분류:건강   
115   http://ko.dbpedia.org/resource/분류:국제_교류   
116  http://ko.dbpedia.org/resource/분류:여행의_형태   
117   http://ko.dbpedia.org/resource/분류:국제_교류   
118  http://ko.dbpedia.org/resource/분류:여행의_형태   

                         redirects.value subject  
0                                    NaN      여행  
1      http://ko.dbpedia.org/resource/여행      여행  
2                                    NaN      영화  
3      http://ko.dbpedia.org/resource/영화      영화  
4                                    NaN      사랑  
..                                   ...     ...  
114    http://ko.dbpedia.org/resource/건강      건강  
115                                  NaN    해외여행  
116                                  NaN    해외여행  
117  http://ko.dbpedia.org/resource/해외여행    해외여행  
118  http://ko.dbpedia.org/resource/해외여행    해외여행  

[119 rows x 5 columns]